## Importing relevant libraries

In [1]:
import numpy as np
import scipy.linalg as la
import scipy.spatial as spat
from scipy.stats import unitary_group
from scipy.stats import moment
from scipy.stats import skew, kurtosis
from scipy.optimize import curve_fit
from scipy.linalg import norm
import matplotlib.pyplot as plt
import math
from dataclasses import dataclass

# Libraries for implementing the VQD algorithm
from qiskit.circuit import QuantumCircuit, Parameter
from qiskit.primitives import Sampler, Estimator
from qiskit_aer import AerSimulator
# from qiskit_ibm_runtime import QiskitRuntimeService, Estimator, Sampler, Session, Options
from qiskit.quantum_info.operators import Operator
from qiskit.quantum_info import SparsePauliOp
from qiskit.circuit.library import RealAmplitudes, TwoLocal, EfficientSU2
from qiskit_algorithms.optimizers import *
from qiskit_algorithms.state_fidelities import ComputeUncompute

from qiskit_algorithms.eigensolvers import EigensolverResult, VQD
from qiskit_algorithms import NumPyMinimumEigensolver, VQE

# Import classical optimizers
from qiskit_algorithms.optimizers import SPSA, P_BFGS, COBYLA, IMFIL, SNOBFIT, NELDER_MEAD, SLSQP, NFT, ADAM, POWELL, GradientDescent, BOBYQA

# Import Statevector and SparsePauliOp
from qiskit.quantum_info import SparsePauliOp, Statevector

# Import noise models
from qiskit_aer.noise import (
    NoiseModel,
    QuantumError,
    ReadoutError,
    depolarizing_error,
    pauli_error,
    thermal_relaxation_error,
)

# Import a fake backend and Qiskit simulators and/or noise libraries
from qiskit_aer import AerSimulator
# from qiskit_aer.primitives import Estimator as AerEstimator 
# from qiskit_aer.noise import NoiseModel

## Construct the Schlogl operator

In [3]:
def TridiagA(lambda_func, mu_func, N):
    """
    Creates tridiagonal stochastic matrix for the Schlogl model
    Inputs lambda and mu model functions, and N desired size of matrix
    Returns stochastic matrix (non-hermitian)
    """
    # initialize diagonals
    d1 = np.zeros(N - 1)
    d2 = np.zeros(N)
    d3 = np.zeros(N - 1)

    # element 1,1
    d2[0] = -lambda_func(0)

    # element N,N
    d2[N - 1] = -mu_func(N - 1)

    # bottom diagonal elements
    for i in range(N - 1):
        d1[i] = lambda_func(i)

    # top diagonal elements
    for i in range(1, N):
        d3[i - 1] = mu_func(i)

    # main diagonal elements
    for i in range(1, N - 1):
        d2[i] = -lambda_func(i) - mu_func(i)

    # putting the diagonals together
    Q = np.diag(d1, k = -1) + np.diag(d2, k = 0) + np.diag(d3, k = 1)
    
    return Q

def get_volume_array(start_V, stop_V, n_operator_qubits):
    # Function to generate the initial volume array (to carry out computations)
    
    num_elements = 2 ** n_operator_qubits
    step_size = (stop_V - start_V)/(num_elements - 1)
    
    # Generate the volume array, given that the step size has been determined
    volume_array = np.arange(start_V, stop_V, step_size)
    
    return volume_array

def get_unitary(matrix, add_half = False):
    """
    Purpose: given a matrix, returns the unitary, hermitian matrix to be diagonalized
    Input: matrix -> the matrix to be diagonalized
    Output: U -> the unitary matrix
            nqubits -> the number of qubis needed to represent the basis of U
            dimension -> the dimension of the original matrix
    """
    assert matrix.ndim == 2, "Error: Only a matrix maybe processed"
    assert matrix.shape[0] == matrix.shape[1], "Error: Only a square matrix maybe processed"

    if np.any(np.transpose(matrix) != matrix):
        matrix_T = np.transpose(matrix)
        matrix = np.dot(matrix_T, matrix)

    ## Finding the dimension of the matrix
    dimension_hermitian = matrix.shape[0]

    ## Finding the number of qubits required to represent the matrix
    nqubits = int(np.ceil(np.log2(dimension_hermitian)))

    ## Construct the relevant matrix
    op_dim = 2 ** nqubits
    op = np.eye(op_dim)
    op[0:dimension_hermitian, 0:dimension_hermitian] = np.copy(matrix)

    if add_half:
        op = op + np.pi * np.eye(op.shape[0])

    U = la.expm(1j*op)
    
    # Get the dimensions of the unitary matrix
    dimension = U.shape[0]

    return U, nqubits, dimension

def find_probability(eigenvector_raw):
    """
    Purpose: Find the probability associated with each basis of an eigenvector
    Input: eigenvector_raw -> Numpy array documenting the number of times each basis is detected within the eigenvector
    Output: eigenvector_prob -> Numpy array documenting the probability of detecting each basis
    """
    count_total = np.sum(eigenvector_raw)
    eigenvector_prob = eigenvector_raw / count_total
    
    return eigenvector_prob

def find_amplitude(eigenvector_prob):
    """
    Purpose: Finding the probability amplitude of each basis using quantum mechanics
    Input: eigenvector_prob -> Numpy array documenting the probability that each basis is measured
    Output: eigenvector -> Numpy array representing the eigenvector
    """
    eigenvector = np.sqrt(eigenvector_prob)
    return eigenvector

def normalize_eigenvector(vector):
    """
    Purpose: Normalizes a vector such that its norm is 1
    Input: vector -> The vector to be normalized
    Output: vector -> The normalized vector
    """
    L2 = np.sum(np.square(vector))
    vector = vector / np.sqrt(L2)

    return vector

def get_similarity(a, b):
    # Function to compute the similarity between 2 zeromodes

    # Get absolute values
    b = np.abs(b)
    
    numerator = np.abs(np.dot(a.conj().T, b))**2
    denominator = np.linalg.norm(a)**2 * np.linalg.norm(b)**2
    
    return numerator / denominator

def get_expectation(matrix, zeromode):
    # Compute the expectation value of the Schlogl operator in the steady-state
    
    # Convert the zeromode into a matrix (column vector)    
    zeromode = np.array(zeromode).reshape(len(zeromode), 1)
    zeromode = np.abs(zeromode) # get rid of all (extraneous) negative values (since this is a PDF)
    
    # Compute the steady-state expectation value
    value = np.dot(matrix, zeromode)
    expectation_value = np.dot(zeromode.T, value)
    
    return expectation_value

def compute_rmsd(list1, list2):
    # Ensure the lists have the same length
    
    if len(list1) != len(list2):
        raise ValueError("Lists must have the same length.")
    
    # Compute the RMSD
    rmsd = np.sqrt(np.mean((np.array(list1) - np.array(list2)) ** 2))
    return rmsd

def get_expectation(matrix, zeromode):
    # Compute the expectation value of the Schlogl operator in the steady-state
    
    # Convert the zeromode into a matrix (column vector)    
    zeromode = np.array(zeromode).reshape(len(zeromode), 1)
    zeromode = np.abs(zeromode) # get rid of all (extraneous) negative values (since this is a PDF)
    
    # Compute the steady-state expectation value
    value = np.dot(matrix, zeromode)
    expectation_value = np.dot(zeromode.T, value)
    
    return expectation_value

def compute_eigenvalues(matrix):
    """
    Computes the two eigenvalues with the highest real parts of a general matrix.

    Parameters:
        matrix (np.ndarray): The matrix for which to compute the eigenvalues.

    Returns:
        list: A list containing the two eigenvalues with the highest real parts [eigenvalue1, eigenvalue2].
    """
    # Compute all eigenvalues
    eigenvalues = np.linalg.eigvals(matrix)
    
    # Sort by real part in descending order and select the two with the lowest real parts
    lowest_two_eigenvalues = sorted(eigenvalues, key=lambda x: x.real, reverse=False)[:2]

    # Print
    print('The lowest two eigenvalues are:')
    print(lowest_two_eigenvalues)
    print()
    
    return lowest_two_eigenvalues

def compute_relative_errors(exact_eigenvalues, vqd_eigenvalues):
    """
    Computes the relative errors for the first and second eigenvalues for each optimizer.

    Parameters:
        exact_eigenvalues (list): List of the two lowest exact eigenvalues [lambda_1, lambda_2].
        vqd_eigenvalues (dict): Dictionary where keys are optimizer names and values are lists of the two
                                lowest VQD eigenvalues computed by each optimizer.

    Returns:
        dict: Dictionary where each key is an optimizer name and the value is a tuple of the relative errors
              (error_first, error_second).
    """
    # Extract the exact eigenvalues for easy reference
    exact_first, exact_second = exact_eigenvalues
    
    # Initialize a dictionary to store relative errors for each optimizer
    relative_errors = {}
    
    for optimizer, eigenvalues in vqd_eigenvalues.items():
        vqd_first, vqd_second = eigenvalues  # VQD-computed first and second eigenvalues for this optimizer
        
        # Calculate relative errors for the first and second eigenvalues
        error_first = abs((vqd_first - exact_first) / exact_first) if exact_first != 0 else np.nan
        error_second = abs((vqd_second - exact_second) / exact_second) if exact_second != 0 else np.nan
        
        # Store the errors in the dictionary
        relative_errors[optimizer] = (error_first, error_second)
    
    return relative_errors

## VQD implementation

In [6]:
# Define the VQD computation with varying ansatz depth
def run_vqd(matrix, ansatz, optimizer, seed):
    """
    Function to compute the zeromode and eigenvalues for different optimizers and ansatz depths,
    averaged over multiple independent VQD runs.

    Args:
        matrix (np.ndarray): The Hamiltonian matrix.
        ansatz (QuantumCircuit): The ansatz circuit.
        optimizer (Optimizer): Classical optimizer for VQD.
        seed (int): Seed value for reproducibility.
        eigenvalues_exact (list): List of exact eigenvalues for reference (classical values).

    Returns:
        zeromode (list): The zeromode statevector obtained from VQD.
        eigenvalues_vqd (list): List of eigenvalues obtained from VQD.
        num_func_calls (int): Number of function calls made by the optimizer.
    """
    
    dimension = matrix.shape[0]
    num_qubits = int(np.log2(dimension))
    
    # Define the qubit Hamiltonian
    qub_hamiltonian = SparsePauliOp.from_operator(matrix)

    # Initial point for the classical optimizer
    seed_value = seed
    np.random.seed(seed_value)
    initial_point = np.random.uniform(-np.pi, np.pi, ansatz.num_parameters)
    
    # Initializing the Estimator, Sampler, and fidelity
    estimator = Estimator()
    sampler = Sampler()
    fidelity = ComputeUncompute(sampler)
    
    # Run the VQE algorithm
    @dataclass
    class VQDLog:
        values: list = None
        parameters: list = None
        
        def __post_init__(self):
            self.values = []
            self.parameters = []

        # Update function to match the expected arguments
        def update(self, count, parameters, mean, _metadata, _extra):
            self.values.append(mean)
            self.parameters.append(parameters)

    log = VQDLog()

    vqd = VQD(estimator,
              fidelity, ansatz, optimizer, k=2, initial_point=initial_point, callback=log.update)
    result = vqd.compute_eigenvalues(qub_hamiltonian)

    # Get the optimizer runtime (not used in the current context, but can be logged)
    time = result.optimizer_times

    # Extract the optimal parameters
    optimal_params = result.optimal_points
    zeromode_points = optimal_params[0]
    final_circuit = ansatz.assign_parameters(zeromode_points)
    zeromode_vqd = Statevector.from_instruction(final_circuit)
    zeromode = zeromode_vqd.data.tolist()

    # Extract the first and second eigenvalues from VQD results
    eigenvalues_vqd = result.eigenvalues

    # Get the number of function calls
    num_func_calls = result.cost_function_evals

    # Get the gate count and circuit depth of the variational ansatz
    decomposed_ansatz = ansatz.decompose()  
    gate_count_dict = decomposed_ansatz.count_ops()
    gate_count = sum(gate_count_dict.values())
    circuit_depth = decomposed_ansatz.depth()  # Depth of the ansatz circuit

    return zeromode, eigenvalues_vqd, gate_count, circuit_depth, num_func_calls

## Estimate resources (use a relative error (in \lambda_1) threshold here)

In [9]:
def estimate_resources(matrix, optimizers, num_qubits, target_relative_error_threshold, exact_second_eigenvalue):
    """
    Computes the minimum ansatz depth required to achieve a target relative error threshold for the second eigenvalue 
    for a set of optimizers and ansatz types. For each optimizer-ansatz pair, at the minimum depth that achieves 
    the relative error threshold, the quantum-computed lowest two eigenvalues of the original matrix H are returned.

    Parameters:
        matrix (np.ndarray): The original matrix H.
        optimizers (list): A list of optimizers to use.
        num_qubits (int): The number of qubits.
        target_relative_error_threshold (float): The relative error threshold for the second eigenvalue.
        exact_second_eigenvalue (float): The exact second eigenvalue of the original matrix H.

    Returns:
        min_depths (dict): Minimum depths for each optimizer-ansatz pair to achieve the relative error threshold.
        eigenvalues (dict): Quantum-computed first and second eigenvalues for each optimizer-ansatz pair at the minimum depth.
        metrics (dict): Number of function calls, gate count, circuit depth, and relative error at the threshold meeting depth.
    """

    # Initialize dictionaries to store results
    min_depths = {}
    eigenvalues = {}
    metrics = {}

    # Define ansatz types
    ansatz_classes = [RealAmplitudes, TwoLocal, EfficientSU2]

    # Loop through each optimizer
    for optimizer in optimizers:
        optimizer_name = optimizer.__class__.__name__
        
        # Loop through each ansatz type
        for AnsatzClass in ansatz_classes:
            ansatz_name = AnsatzClass.__name__
            pair_name = f"{optimizer_name}-{ansatz_name}"
            print(f"\nRunning VQD for optimizer-ansatz pair: {pair_name}")
            
            current_depth = 1
            max_depth = 10
            converged = False  # Flag to check if convergence occurs
            
            while current_depth <= max_depth:  # Loop up to max_depth
                best_relative_error = np.inf  # Initialize to a high value
                best_run_result = None  # Track best eigenvalues for the run with the best relative error
                best_run_metrics = {}  # Track metrics for the run that meets the threshold
                best_relative_error_value = None  # Store the relative error at the best run
                
                # Initialize ansatz with appropriate configurations
                if AnsatzClass == RealAmplitudes:
                    ansatz = AnsatzClass(num_qubits=num_qubits, entanglement='full', reps=current_depth)
                elif AnsatzClass == TwoLocal:
                    ansatz = AnsatzClass(num_qubits=num_qubits, rotation_blocks=['ry'], entanglement_blocks='cx', reps=current_depth)
                elif AnsatzClass == EfficientSU2:
                    ansatz = AnsatzClass(num_qubits=num_qubits, su2_gates=['ry'], entanglement='sca', reps=current_depth)
                
                # Perform multiple independent VQD runs
                for run in range(10):  # 10 independent VQD runs
                    seed = run + 1

                    # Run VQD and capture additional metrics
                    zeromode, eigenvalues_quantum, gate_count, circuit_depth, func_calls = run_vqd(
                        matrix=matrix,
                        ansatz=ansatz,
                        optimizer=optimizer,
                        seed=seed,
                    )
                    
                    # Calculate the relative error in the second eigenvalue
                    second_eigenvalue = eigenvalues_quantum[1]
                    relative_error_in_second_eigenvalue = abs(second_eigenvalue - exact_second_eigenvalue) / abs(exact_second_eigenvalue)

                    # Update if this run provides a lower relative error
                    if relative_error_in_second_eigenvalue < best_relative_error:
                        best_relative_error = relative_error_in_second_eigenvalue
                        best_relative_error_value = relative_error_in_second_eigenvalue
                        best_run_result = eigenvalues_quantum  # Store the two eigenvalues
                        best_run_metrics = {
                            "run_number": run + 1,
                            "function_calls": func_calls,
                            "gate_count": gate_count,
                            "circuit_depth": circuit_depth,
                            "relative_error": best_relative_error_value
                        }
                
                # Check if the best relative error in the second eigenvalue meets the threshold
                if best_relative_error <= target_relative_error_threshold:
                    min_depths[pair_name] = current_depth
                    eigenvalues[pair_name] = best_run_result
                    metrics[pair_name] = best_run_metrics
                    print(f"Minimum ansatz depth for {pair_name} to achieve target relative error threshold: {current_depth}")
                    print(f"Best estimate for lowest two eigenvalues at this depth: {best_run_result}")
                    print(f"Metrics at threshold: Function calls = {best_run_metrics['function_calls']}, "
                          f"Gate count = {best_run_metrics['gate_count']}, Circuit depth = {best_run_metrics['circuit_depth']}, "
                          f"Relative Error = {best_run_metrics['relative_error']}")
                    print(f"Relative error threshold met at run number: {best_run_metrics['run_number']}")
                    
                    converged = True
                    break  # Exit if threshold is met

                current_depth += 1  # Increase depth if threshold not met
            
            # If no convergence occurs within max_depth, mark as "did not converge"
            if not converged:
                min_depths[pair_name] = "Did not converge"
                eigenvalues[pair_name] = "Did not converge"
                metrics[pair_name] = "Did not converge"
                print(f"{pair_name} did not converge within {max_depth} depths.")
    
    return min_depths, eigenvalues, metrics

## Get the matrix and the zeromode

In [12]:
def get_zeromode(num_operator_qubits, V):
    # Function to get the matrix and the zeromode

    ## Computing the block diagonal representation of the Schlogl operator matrix
    # Defining parameters
    a = 1
    b = 1
    k1 = 3
    k2 = 0.6
    k3 = 0.25
    k4 = 2.95
    
    # Number of qubits
    num_operator_qubits = num_operator_qubits
    
    # Matrix dimensions
    N = 2 ** num_operator_qubits
    
    # Generating the basis size array
    x_axis = []
    
    for i in range(N):
        x_axis.append(i)
    
    # # Constructing the Schlogl operator for V = 1.1
    # # Get the volume array
    # start_V = 0.1
    # stop_V = 1.6
    # volume_array = get_volume_array(start_V, stop_V, num_operator_qubits)
    
    # # For system volume V = 1.1
    # volume_array = np.arange(0.1, 10.6, 0.1)
    
    # # Construct the matrix representation of the operator
    # for i, V in enumerate(volume_array):
        
    #     # Birth and death rates
    #     lambda_fn = lambda n: ((a*k1*n*(n-1))/V + b*k3*V)
    #     mu_fn = lambda n: ((k2*n*(n-1)*(n-2))/V**2 + n*k4)
    
    #     # stochastic matrix Q of dimension N x N
    #     Q = TridiagA(lambda_fn, mu_fn, N)
        
    #     i += 1
    # ######################################################################  
    # Construct the matrix
    # Birth and death rates
    lambda_fn = lambda n: ((a*k1*n*(n-1))/V + b*k3*V)
    mu_fn = lambda n: ((k2*n*(n-1)*(n-2))/V**2 + n*k4)

    # stochastic matrix Q of dimension N x N
    Q = TridiagA(lambda_fn, mu_fn, N)
    
    # Print the original Schlogl operator matrix
    print('The Schlogl operator matrix is:')
    print(Q)
    print()
        
    # Compute the Hermitian form of the matrix
    hermitian_matrix = np.dot(Q.T, Q)
    
    # # Print the volume array
    # print('The volume array is:')
    # print(volume_array)
    # print()
    
    # Print the volume parameter for which the simulations are being run
    print('The volume parameter is:')
    print(V)
    print()
    
    # Print the Hermitian matrix (block diagonal form)
    print('The Hermitian form of the Schlogl matrix is:')
    print(hermitian_matrix)
    print()
    
   ## Get the classical zeromode
    A, P = la.eig(Q)
    
    A_real = np.real(A)
    index = np.where(A_real == np.amax(A_real))[0][0]
    
    eigenvalue = A[index]
    zeromode_classic = P[:, index]
    
    zeromode_classic = np.real(normalize_eigenvector(zeromode_classic))
    zeromode_classic = np.reshape(zeromode_classic, (zeromode_classic.size, 1))
    
    print("the available eigenvalues are: \n" + str(A))
    print()
    
    print("The minimum eigenvalue located is: \n" + str(eigenvalue))
    print()
    
    print("The minimum zeromode located is: \n" + str(np.real(zeromode_classic)))

    return Q, hermitian_matrix, zeromode_classic

## Quantum (VQD) analysis

### For V = 1.1 (N = 2)

### Get the matrix and classical eigenvalues

In [15]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(2, 1.1)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[ -0.275        2.95         0.           0.        ]
 [  0.275       -3.225        5.9          0.        ]
 [  0.           0.275      -11.62954545  11.82520661]
 [  0.           0.           5.72954545 -11.82520661]]

The volume parameter is:
1.1

The Hermitian form of the Schlogl matrix is:
[[ 1.51250000e-01 -1.69812500e+00  1.62250000e+00  0.00000000e+00]
 [-1.69812500e+00  1.91787500e+01 -2.22256250e+01  3.25193182e+00]
 [ 1.62250000e+00 -2.22256250e+01  2.02884019e+02 -2.05274837e+02]
 [ 0.00000000e+00  3.25193182e+00 -2.05274837e+02  2.79671023e+02]]

the available eigenvalues are: 
[  0.        +0.j  -2.60510311+0.j  -4.34244163+0.j -20.00720732+0.j]

The minimum eigenvalue located is: 
0j

The minimum zeromode located is: 
[[0.99567159]
 [0.09281684]
 [0.00432621]
 [0.00209613]]
The lowest two eigenvalues are:
[1.0754013022257892e-14, 9.002123036682548]



### Estimate resources (fix at 5000 optimization iterations)

In [49]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_2, eigenvalues_N_2, metrics_N_2 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes
Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [6.84226009e-09+0.j 9.00212303e+00+0.j]
Metrics at threshold: Function calls = [91 93], Gate count = 5, Circuit depth = 3, Relative Error = 3.8507069682938684e-10
Relative error threshold met at run number: 4

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [5.74965178e-08+0.j 9.00212304e+00+0.j]
Metrics at threshold: Function calls = [ 67 300], Gate count = 5, Circuit depth = 3, Relative Error = 3.314551313825821e-11
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [6.84226009e-09+0.j 9.00212303e+00+0.j]
Metrics at threshold: Function calls = [91 93], Gate count = 5, Circuit depth = 3, Relative Error = 3.8507069682938684e-10
Relative error threshold met at run number: 4

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [7.99360578e-13+0.j 9.00212304e+00+0.j]
Metrics at threshold: Function calls = [135 365], Gate count = 5, Circuit depth = 3, Relative Error = 5.919793027139756e-16
Relative error threshold met at run number: 7

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [4.95603558e-13+0.j 9.00212304e+00+0.j]
Metrics at threshold: Function calls = [110 215], Gate count = 5, Circuit depth = 3, Relative Error = 1.973264342379919e-15
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [7.99360578e-13+0.j 9.00212304e+00+0.j]
Metrics at threshold: Function calls = [135 365], Gate count = 5, Circuit depth = 3, Relative Error = 5.919793027139756e-16
Relative error threshold met at run number: 7

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
Minimum ansatz depth for NELDER_MEAD-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3.04350838e-08+0.j 9.00212304e+00+0.j]
Metrics at threshold: Function calls = [362 261], Gate count = 5, Circuit depth = 3, Relative Error = 4.507391582058824e-10
Relative error threshold met at run number: 9

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
Minimum ansatz depth for NELDER_MEAD-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3.

### Print resource estimates and eigenvalues

In [51]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_2)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_2)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_2)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 1, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 1, 'P_BFGS-RealAmplitudes': 1, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 1, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 1, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 1}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([6.84226009e-09+0.j, 9.00212303e+00+0.j]), 'SLSQP-TwoLocal': array([5.74965178e-08+0.j, 9.00212304e+00+0.j]), 'SLSQP-EfficientSU2': array([6.84226009e-09+0.j, 9.00212303e+00+0.j]), 'P_BFGS-RealAmplitudes': array([7.99360578e-13+0.j, 9.00212304e+00+0.j]), 'P_BFGS-TwoLocal': array([4.95603558e-13+0.j, 9.00212304e+00+0.j]), 'P_BFGS-EfficientSU2': array([7.99360578e-13+0.j, 9.00212304e+00+0.j]), 'NELDER_MEAD-RealAmplitudes': array([3.04350838e-08+0.j, 9.00212304e+00+0.j]), 'NELDER_MEAD-TwoLocal': array([3.04350838e-08+0.j, 9.00212304e+00+0.j]), 'NELDER_MEAD-EfficientSU2': array([3.04350838e-08+0.j, 

### For V = 5.5 (N = 2)

### Get the matrix and the zeromode

In [56]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(2, 5.5)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[-1.375       2.95        0.          0.        ]
 [ 1.375      -4.325       5.9         0.        ]
 [ 0.          1.375      -8.36590909  8.96900826]
 [ 0.          0.          2.46590909 -8.96900826]]

The volume parameter is:
5.5

The Hermitian form of the Schlogl matrix is:
[[  3.78125    -10.003125     8.1125       0.        ]
 [-10.003125    29.29875    -37.020625    12.33238636]
 [  8.1125     -37.020625   110.87914256 -97.15066679]
 [  0.          12.33238636 -97.15066679 160.8862185 ]]

the available eigenvalues are: 
[ 4.44089210e-16+0.j -2.84354832e+00+0.j -6.37631943e+00+0.j
 -1.38150496e+01+0.j]

The minimum eigenvalue located is: 
(4.440892098500626e-16+0j)

The minimum zeromode located is: 
[[-0.90169082]
 [-0.42027962]
 [-0.09794652]
 [-0.02692909]]
The lowest two eigenvalues are:
[-4.257371493713317e-15, 9.1459297986593]



### Estimate resources (fix at 5000 optimization iterations)

In [58]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_2, eigenvalues_N_2, metrics_N_2 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes
Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3.24965863e-08+0.j 9.14592981e+00+0.j]
Metrics at threshold: Function calls = [109  92], Gate count = 5, Circuit depth = 3, Relative Error = 1.0963103644061048e-09
Relative error threshold met at run number: 1

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.15060148e-08+0.j 9.14592980e+00+0.j]
Metrics at threshold: Function calls = [110 120], Gate count = 5, Circuit depth = 3, Relative Error = 1.9085261445967545e-10
Relative error threshold met at run number: 10

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3.24965863e-08+0.j 9.14592981e+00+0.j]
Metrics at threshold: Function calls = [109  92], Gate count = 5, Circuit depth = 3, Relative Error = 1.0963103644061048e-09
Relative error threshold met at run number: 1

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.50102153e-13+0.j 9.14592980e+00+0.j]
Metrics at threshold: Function calls = [115 180], Gate count = 5, Circuit depth = 3, Relative Error = 2.4860640793084018e-14
Relative error threshold met at run number: 4

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.38555833e-13+0.j 9.14592980e+00+0.j]
Metrics at threshold: Function calls = [100 300], Gate count = 5, Circuit depth = 3, Relative Error = 4.0786988801153464e-15
Relative error threshold met at run number: 7

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.50102153e-13+0.j 9.14592980e+00+0.j]
Metrics at threshold: Function calls = [115 180], Gate count = 5, Circuit depth = 3, Relative Error = 2.4860640793084018e-14
Relative error threshold met at run number: 4

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
Minimum ansatz depth for NELDER_MEAD-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3.58511398e-09+0.j 9.14592980e+00+0.j]
Metrics at threshold: Function calls = [211 315], Gate count = 5, Circuit depth = 3, Relative Error = 4.636490085534549e-11
Relative error threshold met at run number: 6

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
Minimum ansatz depth for NELDER_MEAD-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [3

### Print resource estimates and eigenvalue metrics

In [60]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_2)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_2)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_2)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 1, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 1, 'P_BFGS-RealAmplitudes': 1, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 1, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 1, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 1}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([3.24965863e-08+0.j, 9.14592981e+00+0.j]), 'SLSQP-TwoLocal': array([1.15060148e-08+0.j, 9.14592980e+00+0.j]), 'SLSQP-EfficientSU2': array([3.24965863e-08+0.j, 9.14592981e+00+0.j]), 'P_BFGS-RealAmplitudes': array([1.50102153e-13+0.j, 9.14592980e+00+0.j]), 'P_BFGS-TwoLocal': array([1.38555833e-13+0.j, 9.14592980e+00+0.j]), 'P_BFGS-EfficientSU2': array([1.50102153e-13+0.j, 9.14592980e+00+0.j]), 'NELDER_MEAD-RealAmplitudes': array([3.58511398e-09+0.j, 9.14592980e+00+0.j]), 'NELDER_MEAD-TwoLocal': array([3.58511398e-09+0.j, 9.14592980e+00+0.j]), 'NELDER_MEAD-EfficientSU2': array([3.58511398e-09+0.j, 

### For V = 10.5 (N = 2)

### Get the matrix and the zeromode

In [62]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(2, 10.5)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[-2.625       2.95        0.          0.        ]
 [ 2.625      -5.575       5.9         0.        ]
 [ 0.          2.625      -9.09642857  8.88265306]
 [ 0.          0.          3.19642857 -8.88265306]]

The volume parameter is:
10.5

The Hermitian form of the Schlogl matrix is:
[[  13.78125     -22.378125     15.4875        0.        ]
 [ -22.378125     46.67375     -56.770625     23.31696429]
 [  15.4875      -56.770625    127.77216837 -109.19318513]
 [   0.           23.31696429 -109.19318513  157.80305081]]

the available eigenvalues are: 
[-1.52577371e+01+0.j -7.74424342e+00+0.j -9.70174270e-16+0.j
 -3.17710106e+00+0.j]

The minimum eigenvalue located is: 
(-9.701742699678762e-16+0j)

The minimum zeromode located is: 
[[-0.71268205]
 [-0.63416623]
 [-0.28215023]
 [-0.10153195]]
The lowest two eigenvalues are:
[-4.3517946982977e-15, 10.364814601313393]



### Estimate resources (fix at 5000 optimization iterations)

In [64]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_2, eigenvalues_N_2, metrics_N_2 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes
Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.78774938e-08+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [65 90], Gate count = 5, Circuit depth = 3, Relative Error = 2.0610512470927613e-10
Relative error threshold met at run number: 1

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [7.04728761e-10+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [90 89], Gate count = 5, Circuit depth = 3, Relative Error = 1.8327737418611545e-12
Relative error threshold met at run number: 8

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.78774938e-08+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [65 90], Gate count = 5, Circuit depth = 3, Relative Error = 2.0610512470927613e-10
Relative error threshold met at run number: 1

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [4.55496751e-13+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [110 105], Gate count = 5, Circuit depth = 3, Relative Error = 1.0283002105074741e-15
Relative error threshold met at run number: 10

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [8.03489220e-14+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [100 215], Gate count = 5, Circuit depth = 3, Relative Error = 5.9984178946269324e-15
Relative error threshold met at run number: 5

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [4.55496751e-13+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [110 105], Gate count = 5, Circuit depth = 3, Relative Error = 1.0283002105074741e-15
Relative error threshold met at run number: 10

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
Minimum ansatz depth for NELDER_MEAD-RealAmplitudes to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: [1.70876069e-08+0.j 1.03648146e+01+0.j]
Metrics at threshold: Function calls = [202 279], Gate count = 5, Circuit depth = 3, Relative Error = 1.8462547576209077e-10
Relative error threshold met at run number: 5

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
Minimum ansatz depth for NELDER_MEAD-TwoLocal to achieve target relative error threshold: 1
Best estimate for lowest two eigenvalues at this depth: 

### Print resource estimates and eigenvalue metrics

In [66]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_2)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_2)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_2)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 1, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 1, 'P_BFGS-RealAmplitudes': 1, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 1, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 1, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 1}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([1.78774938e-08+0.j, 1.03648146e+01+0.j]), 'SLSQP-TwoLocal': array([7.04728761e-10+0.j, 1.03648146e+01+0.j]), 'SLSQP-EfficientSU2': array([1.78774938e-08+0.j, 1.03648146e+01+0.j]), 'P_BFGS-RealAmplitudes': array([4.55496751e-13+0.j, 1.03648146e+01+0.j]), 'P_BFGS-TwoLocal': array([8.03489220e-14+0.j, 1.03648146e+01+0.j]), 'P_BFGS-EfficientSU2': array([4.55496751e-13+0.j, 1.03648146e+01+0.j]), 'NELDER_MEAD-RealAmplitudes': array([1.70876069e-08+0.j, 1.03648146e+01+0.j]), 'NELDER_MEAD-TwoLocal': array([1.70876069e-08+0.j, 1.03648146e+01+0.j]), 'NELDER_MEAD-EfficientSU2': array([1.70876069e-08+0.j, 

### For N = 3

### For V = 1.1

### Get the matrix and the zeromode

In [15]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(3, 1.1)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[  -0.275         2.95          0.            0.            0.
     0.            0.            0.        ]
 [   0.275        -3.225         5.9           0.            0.
     0.            0.            0.        ]
 [   0.            0.275       -11.62954545   11.82520661    0.
     0.            0.            0.        ]
 [   0.            0.            5.72954545  -28.46384298   23.70082645
     0.            0.            0.        ]
 [   0.            0.            0.           16.63863636  -56.70309917
    44.50206612    0.            0.        ]
 [   0.            0.            0.            0.           33.00227273
   -99.32252066   77.20413223    0.        ]
 [   0.            0.            0.            0.            0.
    54.82045455 -159.29731405  124.7822314 ]
 [   0.            0.            0.            0.            0.
     0.           82.09318182 -124.7822314 ]]

The volume parameter is:
1.1

The Hermitian form of the Schlogl matrix

### Estimate resources (fix at 5000 optimization iterations)

In [17]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_3, eigenvalues_N_3, metrics_N_3 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes


C:\Users\Owner\anaconda3\Lib\site-packages\scipy\optimize\_slsqp_py.py:437: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  fx = wrapped_fun(x)
C:\Users\Owner\anaconda3\Lib\site-packages\scipy\optimize\_slsqp_py.py:441: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  g = append(wrapped_grad(x), 0.0)


Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.97881111e-05+0.j 4.50260766e+00+0.j]
Metrics at threshold: Function calls = [ 494 2515], Gate count = 15, Circuit depth = 9, Relative Error = 4.0779579019260385e-06
Relative error threshold met at run number: 8

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.02260096e-05+0.j 4.50262173e+00+0.j]
Metrics at threshold: Function calls = [ 868 4422], Gate count = 15, Circuit depth = 9, Relative Error = 9.527839370856841e-07
Relative error threshold met at run number: 5

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.37069947e-07+0.j 4.50262697e+00+0.j]
Metrics at threshold: Function calls = [ 648 1282], Gate count = 15, Circuit depth = 9, Relative Error = 2.1069280056367884e-07
Relative error threshold met at run number: 3

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


...

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.11604079e-04+0.j 4.50256232e+00+0.j]
Metrics at threshold: Function calls = [1000 5050], Gate count = 15, Circuit depth = 9, Relative Error = 1.4146364505281603e-05
Relative error threshold met at run number: 5

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.08442191e-06+0.j 4.50262604e+00+0.j]
Metrics at threshold: Function calls = [5120 5050], Gate count = 15, Circuit depth = 9, Relative Error = 5.326318551087695e-09
Relative error threshold met at run number: 3

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.40652298e-09+0.j 4.50262653e+00+0.j]
Metrics at threshold: Function calls = [2100 5030], Gate count = 15, Circuit depth = 9, Relative Error = 1.1398591331110709e-07
Relative error threshold met at run number: 1

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
NELDER_MEAD-RealAmplitudes did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
NELDER_MEAD-TwoLocal did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: NELDER_MEAD-EfficientSU2
NELDER_MEAD-EfficientSU2 did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: POWELL-RealAmplitudes
POWELL-RealAmplitudes did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: POWELL-TwoLocal
POWELL-TwoLocal did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: PO

### Print resource estimates and eigenvalue metrics

In [21]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_3)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_3)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_3)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 2, 'SLSQP-TwoLocal': 2, 'SLSQP-EfficientSU2': 2, 'P_BFGS-RealAmplitudes': 2, 'P_BFGS-TwoLocal': 2, 'P_BFGS-EfficientSU2': 2, 'NELDER_MEAD-RealAmplitudes': 'Did not converge', 'NELDER_MEAD-TwoLocal': 'Did not converge', 'NELDER_MEAD-EfficientSU2': 'Did not converge', 'POWELL-RealAmplitudes': 'Did not converge', 'POWELL-TwoLocal': 'Did not converge', 'POWELL-EfficientSU2': 'Did not converge'}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([2.97881111e-05+0.j, 4.50260766e+00+0.j]), 'SLSQP-TwoLocal': array([1.02260096e-05+0.j, 4.50262173e+00+0.j]), 'SLSQP-EfficientSU2': array([1.37069947e-07+0.j, 4.50262697e+00+0.j]), 'P_BFGS-RealAmplitudes': array([1.11604079e-04+0.j, 4.50256232e+00+0.j]), 'P_BFGS-TwoLocal': array([1.08442191e-06+0.j, 4.50262604e+00+0.j]), 'P_BFGS-EfficientSU2': array([2.40652298e-09+0.j, 4.50262653e+00+0.j]), 'NELDER_MEAD-RealAmplitudes': 'Did not converge', 'NELDER_MEAD-TwoLocal': 'Did not converge', 'NELDER_MEA

### For V = 5.5 (N = 3)

### Get the matrix and the zeromode

In [16]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(3, 5.5)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[ -1.375        2.95         0.           0.           0.
    0.           0.           0.        ]
 [  1.375       -4.325        5.9          0.           0.
    0.           0.           0.        ]
 [  0.           1.375       -8.36590909   8.96900826   0.
    0.           0.           0.        ]
 [  0.           0.           2.46590909 -13.61673554  12.27603306
    0.           0.           0.        ]
 [  0.           0.           0.           4.64772727 -20.1964876
   15.94008264   0.           0.        ]
 [  0.           0.           0.           0.           7.92045455
  -28.22417355  20.08016529   0.        ]
 [  0.           0.           0.           0.           0.
   12.28409091 -37.81880165  24.81528926]
 [  0.           0.           0.           0.           0.
    0.          17.73863636 -24.81528926]]

The volume parameter is:
5.5

The Hermitian form of the Schlogl matrix is:
[[    3.78125      -10.003125       8.1125         0.
      

### Estimate resources (fix at 5000 optimization iterations)

In [19]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_3, eigenvalues_N_3, metrics_N_3 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes


C:\Users\Owner\anaconda3\Lib\site-packages\scipy\optimize\_slsqp_py.py:437: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  fx = wrapped_fun(x)


Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.08512458e-06+0.j 4.70567122e+00+0.j]
Metrics at threshold: Function calls = [382 860], Gate count = 15, Circuit depth = 9, Relative Error = 1.7155146317123667e-08
Relative error threshold met at run number: 6

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.50146503e-05+0.j 4.70567186e+00+0.j]
Metrics at threshold: Function calls = [ 510 1381], Gate count = 15, Circuit depth = 9, Relative Error = 1.1877223409725429e-07
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.34822018e-04+0.j 4.70555064e+00+0.j]
Metrics at threshold: Function calls = [519 625], Gate count = 15, Circuit depth = 9, Relative Error = 2.5641322654209395e-05
Relative error threshold met at run number: 6

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


...

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.68941565e-06+0.j 4.70567066e+00+0.j]
Metrics at threshold: Function calls = [5010 3740], Gate count = 15, Circuit depth = 9, Relative Error = 1.3574511218849618e-07
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.22385665e-09+0.j 4.70567130e+00+0.j]
Metrics at threshold: Function calls = [2070 2770], Gate count = 15, Circuit depth = 9, Relative Error = 1.0277806581427619e-11
Relative error threshold met at run number: 8

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [8.71409611e-11+0.j 4.70567130e+00+0.j]
Metrics at threshold: Function calls = [1790 5280], Gate count = 15, Circuit depth = 9, Relative Error = 1.2349203718920088e-10
Relative error threshold met at run number: 7

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
Minimum ansatz depth for NELDER_MEAD-RealAmplitudes to achieve target relative error threshold: 3
Best estimate for lowest two eigenvalues at this depth: [13.99155143+0.j  4.66500975+0.j]
Metrics at threshold: Function calls = [1000 1000], Gate count = 21, Circuit depth = 13, Relative Error = 0.00864096681942278
Relative error threshold met at run number: 9

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
Minimum ansatz depth for NELDER_MEAD-TwoLocal to achieve target relative error threshold: 3
Best estimate for lowest two eigenvalues at this depth: [13

### Print resource estimates and eigenvalue metrics

In [22]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_3)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_3)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_3)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 2, 'SLSQP-TwoLocal': 2, 'SLSQP-EfficientSU2': 2, 'P_BFGS-RealAmplitudes': 2, 'P_BFGS-TwoLocal': 2, 'P_BFGS-EfficientSU2': 2, 'NELDER_MEAD-RealAmplitudes': 3, 'NELDER_MEAD-TwoLocal': 3, 'NELDER_MEAD-EfficientSU2': 'Did not converge', 'POWELL-RealAmplitudes': 7, 'POWELL-TwoLocal': 'Did not converge', 'POWELL-EfficientSU2': 'Did not converge'}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([1.08512458e-06+0.j, 4.70567122e+00+0.j]), 'SLSQP-TwoLocal': array([2.50146503e-05+0.j, 4.70567186e+00+0.j]), 'SLSQP-EfficientSU2': array([2.34822018e-04+0.j, 4.70555064e+00+0.j]), 'P_BFGS-RealAmplitudes': array([1.68941565e-06+0.j, 4.70567066e+00+0.j]), 'P_BFGS-TwoLocal': array([2.22385665e-09+0.j, 4.70567130e+00+0.j]), 'P_BFGS-EfficientSU2': array([8.71409611e-11+0.j, 4.70567130e+00+0.j]), 'NELDER_MEAD-RealAmplitudes': array([13.99155143+0.j,  4.66500975+0.j]), 'NELDER_MEAD-TwoLocal': array([13.99155143+0.j,  4.66500975+0.j]), 'NELDER_MEAD-Eff

### For V = 10.5 (N = 3)

### Get the matrix and the zeromode

In [16]:
## Matrix and zeromode
Q, hermitian_matrix, zeromode = get_zeromode(3, 10.5)

## Get the classical eigenvalues
classical_eigenvalues = compute_eigenvalues(hermitian_matrix)
second_eigenvalue = classical_eigenvalues[1]

The Schlogl operator matrix is:
[[ -2.625        2.95         0.           0.           0.
    0.           0.           0.        ]
 [  2.625       -5.575        5.9          0.           0.
    0.           0.           0.        ]
 [  0.           2.625       -9.09642857   8.88265306   0.
    0.           0.           0.        ]
 [  0.           0.           3.19642857 -13.22193878  11.93061224
    0.           0.           0.        ]
 [  0.           0.           0.           4.33928571 -17.98418367
   15.07653061   0.           0.        ]
 [  0.           0.           0.           0.           6.05357143
  -23.41581633  18.35306122   0.        ]
 [  0.           0.           0.           0.           0.
    8.33928571 -29.5494898   21.79285714]
 [  0.           0.           0.           0.           0.
    0.          11.19642857 -21.79285714]]

The volume parameter is:
10.5

The Hermitian form of the Schlogl matrix is:
[[  13.78125     -22.378125     15.4875        0.         

### Estimate resources (fix at 5000 optimization iterations)

In [19]:
## Get the optimizers
maxiter = 5000
optimizers = [SLSQP(maxiter = maxiter), P_BFGS(maxfun = maxiter), NELDER_MEAD(maxiter = maxiter), POWELL(maxiter = maxiter)]

# Define parameters
dimension = Q.shape[0]
num_qubits = int(np.log2(dimension))
target_error_threshold = 0.01

# Estimate min. ansatz depths
min_depths_N_3, eigenvalues_N_3, metrics_N_3 = \
estimate_resources(hermitian_matrix, optimizers, num_qubits, target_error_threshold, second_eigenvalue)


Running VQD for optimizer-ansatz pair: SLSQP-RealAmplitudes


C:\Users\Owner\anaconda3\Lib\site-packages\scipy\optimize\_slsqp_py.py:437: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  fx = wrapped_fun(x)
C:\Users\Owner\anaconda3\Lib\site-packages\scipy\optimize\_slsqp_py.py:441: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  g = append(wrapped_grad(x), 0.0)


Minimum ansatz depth for SLSQP-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [7.36790315e-07+0.j 5.12551644e+00+0.j]
Metrics at threshold: Function calls = [807 875], Gate count = 15, Circuit depth = 9, Relative Error = 6.334001295596536e-09
Relative error threshold met at run number: 3

Running VQD for optimizer-ansatz pair: SLSQP-TwoLocal
Minimum ansatz depth for SLSQP-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [1.11465441e-07+0.j 5.12551649e+00+0.j]
Metrics at threshold: Function calls = [644 854], Gate count = 15, Circuit depth = 9, Relative Error = 2.0652077262411446e-09
Relative error threshold met at run number: 6

Running VQD for optimizer-ansatz pair: SLSQP-EfficientSU2


For Windows, using only current process. Multiple core use not supported.


Minimum ansatz depth for SLSQP-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.02232143e-07+0.j 5.12551648e+00+0.j]
Metrics at threshold: Function calls = [ 321 1540], Gate count = 15, Circuit depth = 9, Relative Error = 1.428901284529451e-09
Relative error threshold met at run number: 3

Running VQD for optimizer-ansatz pair: P_BFGS-RealAmplitudes


...

Minimum ansatz depth for P_BFGS-RealAmplitudes to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [2.92635427e-09+0.j 5.12551648e+00+0.j]
Metrics at threshold: Function calls = [1620 3610], Gate count = 15, Circuit depth = 9, Relative Error = 9.277470741554739e-11
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: P_BFGS-TwoLocal


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-TwoLocal to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [9.09934350e-10+0.j 5.12551648e+00+0.j]
Metrics at threshold: Function calls = [4480 1340], Gate count = 15, Circuit depth = 9, Relative Error = 1.6652750319646207e-12
Relative error threshold met at run number: 2

Running VQD for optimizer-ansatz pair: P_BFGS-EfficientSU2


For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current process. Multiple core use not supported.
For Windows, using only current proces

Minimum ansatz depth for P_BFGS-EfficientSU2 to achieve target relative error threshold: 2
Best estimate for lowest two eigenvalues at this depth: [8.72484307e-11+0.j 5.12551648e+00+0.j]
Metrics at threshold: Function calls = [1140 2060], Gate count = 15, Circuit depth = 9, Relative Error = 2.1973659282341903e-11
Relative error threshold met at run number: 3

Running VQD for optimizer-ansatz pair: NELDER_MEAD-RealAmplitudes
NELDER_MEAD-RealAmplitudes did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: NELDER_MEAD-TwoLocal
NELDER_MEAD-TwoLocal did not converge within 10 depths.

Running VQD for optimizer-ansatz pair: NELDER_MEAD-EfficientSU2
Minimum ansatz depth for NELDER_MEAD-EfficientSU2 to achieve target relative error threshold: 3
Best estimate for lowest two eigenvalues at this depth: [0.01698828+0.j 5.1692388 +0.j]
Metrics at threshold: Function calls = [1000 1000], Gate count = 21, Circuit depth = 13, Relative Error = 0.008530325387315983
Relative error th

### Print resource estimates and eigenvalue metrics

In [22]:
## Print the resource estimates
print('The min. ansatz depths are:')
print(min_depths_N_3)
print()

## Print the eigenvalues
print('The eigenvalues are:')
print(eigenvalues_N_3)
print()

## Print the performance metrics
print('The performance metrics are:')
print(metrics_N_3)
print()

The min. ansatz depths are:
{'SLSQP-RealAmplitudes': 2, 'SLSQP-TwoLocal': 2, 'SLSQP-EfficientSU2': 2, 'P_BFGS-RealAmplitudes': 2, 'P_BFGS-TwoLocal': 2, 'P_BFGS-EfficientSU2': 2, 'NELDER_MEAD-RealAmplitudes': 'Did not converge', 'NELDER_MEAD-TwoLocal': 'Did not converge', 'NELDER_MEAD-EfficientSU2': 3, 'POWELL-RealAmplitudes': 'Did not converge', 'POWELL-TwoLocal': 'Did not converge', 'POWELL-EfficientSU2': 'Did not converge'}

The eigenvalues are:
{'SLSQP-RealAmplitudes': array([7.36790315e-07+0.j, 5.12551644e+00+0.j]), 'SLSQP-TwoLocal': array([1.11465441e-07+0.j, 5.12551649e+00+0.j]), 'SLSQP-EfficientSU2': array([2.02232143e-07+0.j, 5.12551648e+00+0.j]), 'P_BFGS-RealAmplitudes': array([2.92635427e-09+0.j, 5.12551648e+00+0.j]), 'P_BFGS-TwoLocal': array([9.09934350e-10+0.j, 5.12551648e+00+0.j]), 'P_BFGS-EfficientSU2': array([8.72484307e-11+0.j, 5.12551648e+00+0.j]), 'NELDER_MEAD-RealAmplitudes': 'Did not converge', 'NELDER_MEAD-TwoLocal': 'Did not converge', 'NELDER_MEAD-EfficientSU2': 

## Visualizing results

### For V = 1.1 (N = 2 and 3)

### All quantum resources

In [47]:
# Helper function to plot data
def plot_metric(data, ax, metric_name, ylabel):
    # Extract the optimizers, ansatze, and the specified metric
    optimizers = ['SLSQP', 'P_BFGS', 'NELDER_MEAD', 'POWELL']
    ansatze = ['RealAmplitudes', 'TwoLocal', 'EfficientSU2']
    colors = ['blue', 'red', 'purple']  # Color map for ansatze
    
    # Data organization by optimizer and ansatz
    optimizer_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}
    failed_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}
    
    for entry in data:
        optimizer, value = entry
        opt, ansatz = optimizer.split('-')
        
        if value == 0:  # Mark as 'Did not converge'
            failed_data[opt][ansatz].append(entry)
        else:
            optimizer_data[opt][ansatz].append(value)

    # Plotting the metric for each optimizer and ansatz
    x_positions = np.arange(len(optimizers))
    offset = 0.1  # Base horizontal offset for non-converging cases
    vertical_offset = 0.5  # Vertical offset for crosses

    for i, opt in enumerate(optimizers):
        for j, ansatz in enumerate(ansatze):
            values = optimizer_data[opt][ansatz]
            failed_cases = failed_data[opt][ansatz]
            
            # Plot the non-converging cases
            if failed_cases:
                for k, _ in enumerate(failed_cases):
                    ax.scatter(
                        x_positions[i] + offset * (j - 1),  # Horizontal offset based on ansatz index
                        0 + vertical_offset * (k - len(failed_cases) // 2),  # Vertical offset to spread crosses
                        color=colors[j], marker='x', s=100, label=f'{ansatz} (NC)' if i == 0 and j == 0 else ""
                    )
            
            # Plot the metric values with solid lines connecting the points
            if values:
                ax.plot(
                    [x_positions[i]], values,
                    marker='o', markersize=7, linestyle='-', color=colors[j],
                    label=ansatz if i == 0 else ""  # Only add the ansatz label once
                )
    
    ax.set_xticks(x_positions)
    ax.set_xticklabels(optimizers)
    ax.set_ylabel(ylabel, fontsize=15)
    ax.tick_params(axis='both', which='major', labelsize=14)
    ax.grid(True)
    ax.legend(fontsize=15)

# Data for 2 qubits and 3 qubits
data_2q = [
    ('SLSQP-RealAmplitudes', 5), ('SLSQP-TwoLocal', 5), ('SLSQP-EfficientSU2', 5),
    ('P_BFGS-RealAmplitudes', 5), ('P_BFGS-TwoLocal', 5), ('P_BFGS-EfficientSU2', 5),
    ('NELDER_MEAD-RealAmplitudes', 5), ('NELDER_MEAD-TwoLocal', 5), ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 5), ('POWELL-TwoLocal', 5), ('POWELL-EfficientSU2', 5),
]

data_3q = [
    ('SLSQP-RealAmplitudes', 15), ('SLSQP-TwoLocal', 15), ('SLSQP-EfficientSU2', 15),
    ('P_BFGS-RealAmplitudes', 15), ('P_BFGS-TwoLocal', 15),
    ('NELDER_MEAD-RealAmplitudes', 0), ('NELDER_MEAD-TwoLocal', 0), ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0),
]

# Create figure and axes for 6 subplots
fig, axs = plt.subplots(4, 2, figsize=(14, 18), dpi=600)  # Adjusted to 4 rows

# Plot gate counts
plot_metric(data_2q, axs[0, 0], 'gate_count', 'Gate count')
axs[0, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 2$', fontsize=15)
plot_metric(data_3q, axs[0, 1], 'gate_count', 'Gate count')
axs[0, 1].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 3$', fontsize=15)

# Get the circuit depths
# Data for circuit depths
circuit_depth_2q = [('SLSQP-RealAmplitudes', 3), ('SLSQP-TwoLocal', 3), ('SLSQP-EfficientSU2', 3),
                    ('P_BFGS-RealAmplitudes', 3), ('P_BFGS-TwoLocal', 3), ('P_BFGS-EfficientSU2', 3),
                    ('NELDER_MEAD-RealAmplitudes', 3), ('NELDER_MEAD-TwoLocal', 3), ('NELDER_MEAD-EfficientSU2', 3),
                    ('POWELL-RealAmplitudes', 3), ('POWELL-TwoLocal', 3), ('POWELL-EfficientSU2', 3)]

circuit_depth_3q = [('SLSQP-RealAmplitudes', 9), ('SLSQP-TwoLocal', 9), ('SLSQP-EfficientSU2', 9),
                    ('P_BFGS-RealAmplitudes', 9), ('P_BFGS-TwoLocal', 9),
                    ('NELDER_MEAD-RealAmplitudes', 0), ('NELDER_MEAD-TwoLocal', 0), ('NELDER_MEAD-EfficientSU2', 0),
                    ('POWELL-RealAmplitudes', 0), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0)]

# Plot circuit depths
plot_metric(circuit_depth_2q, axs[1, 0], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depth_3q, axs[1, 1], 'circuit_depth', 'Circuit depth')

# Function calls data (two values for each: \lambda_0 and \lambda_1)
data_2q_function_calls = [
    ('SLSQP-RealAmplitudes', [91, 93]), ('SLSQP-TwoLocal', [67, 300]), ('SLSQP-EfficientSU2', [91, 93]),
    ('P_BFGS-RealAmplitudes', [135, 365]), ('P_BFGS-TwoLocal', [110, 215]), ('P_BFGS-EfficientSU2', [135, 365]),
    ('NELDER_MEAD-RealAmplitudes', [362, 261]), ('NELDER_MEAD-TwoLocal', [362, 261]), ('NELDER_MEAD-EfficientSU2', [362, 261]),
    ('POWELL-RealAmplitudes', [468, 320]), ('POWELL-TwoLocal', [952, 692]), ('POWELL-EfficientSU2', [468, 320])
]

data_3q_function_calls = [
    ('SLSQP-RealAmplitudes', [494, 2515]), ('SLSQP-TwoLocal', [868, 4422]), ('SLSQP-EfficientSU2', [648, 1282]),
    ('P_BFGS-RealAmplitudes', [1000, 5050]), ('P_BFGS-TwoLocal', [5120, 5050]), ('P_BFGS-EfficientSU2', [2100, 5030]),
    ('NELDER_MEAD-RealAmplitudes', [0, 0]), ('NELDER_MEAD-TwoLocal', [0, 0]), ('NELDER_MEAD-EfficientSU2', [0, 0]),
    ('POWELL-RealAmplitudes', [0, 0]), ('POWELL-TwoLocal', [0, 0]), ('POWELL-EfficientSU2', [0, 0])
]

# Plot for function calls (\lambda_0)
plot_metric([(opt, calls[0]) for opt, calls in data_2q_function_calls], axs[2, 0], 'function_calls', r'Function calls ($\lambda_0$)')
plot_metric([(opt, calls[0]) for opt, calls in data_3q_function_calls], axs[2, 1], 'function_calls', r'Function calls ($\lambda_0$)')

# Plot for function calls (\lambda_1)
plot_metric([(opt, calls[1]) for opt, calls in data_2q_function_calls], axs[3, 0], 'function_calls', r'Function calls ($\lambda_1$)')
plot_metric([(opt, calls[1]) for opt, calls in data_3q_function_calls], axs[3, 1], 'function_calls', r'Function calls ($\lambda_1$)')

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.show()

### For V = 5.5 (N = 2 and 3)

### All quantum resources

In [52]:
# Data for 2 qubits
data_2q = [
    ('SLSQP-RealAmplitudes', 5), ('SLSQP-TwoLocal', 5), ('SLSQP-EfficientSU2', 5),
    ('P_BFGS-RealAmplitudes', 5), ('P_BFGS-TwoLocal', 5), ('P_BFGS-EfficientSU2', 5),
    ('NELDER_MEAD-RealAmplitudes', 5), ('NELDER_MEAD-TwoLocal', 5), ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 5), ('POWELL-TwoLocal', 5), ('POWELL-EfficientSU2', 5),
]

# Data for 3 qubits
data_3q = [
    ('SLSQP-RealAmplitudes', 15), ('SLSQP-TwoLocal', 15), ('SLSQP-EfficientSU2', 15),
    ('P_BFGS-RealAmplitudes', 15), ('P_BFGS-TwoLocal', 15),
    ('NELDER_MEAD-RealAmplitudes', 0), ('NELDER_MEAD-TwoLocal', 0), ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0),
]

# Data for circuit depths
circuit_depth_2q = [('SLSQP-RealAmplitudes', 3), ('SLSQP-TwoLocal', 3), ('SLSQP-EfficientSU2', 3),
                    ('P_BFGS-RealAmplitudes', 3), ('P_BFGS-TwoLocal', 3), ('P_BFGS-EfficientSU2', 3),
                    ('NELDER_MEAD-RealAmplitudes', 3), ('NELDER_MEAD-TwoLocal', 3), ('NELDER_MEAD-EfficientSU2', 3),
                    ('POWELL-RealAmplitudes', 3), ('POWELL-TwoLocal', 3), ('POWELL-EfficientSU2', 3)]

circuit_depth_3q = [('SLSQP-RealAmplitudes', 9), ('SLSQP-TwoLocal', 9), ('SLSQP-EfficientSU2', 9),
                    ('P_BFGS-RealAmplitudes', 9), ('P_BFGS-TwoLocal', 9),
                    ('NELDER_MEAD-RealAmplitudes', 13), ('NELDER_MEAD-TwoLocal', 13), ('NELDER_MEAD-EfficientSU2', 0),
                    ('POWELL-RealAmplitudes', 29), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0)]

# Data for function calls (two values for each: \lambda_0 and \lambda_1)
data_2q_function_calls = [
    ('SLSQP-RealAmplitudes', [109, 92]), ('SLSQP-TwoLocal', [110, 120]), ('SLSQP-EfficientSU2', [109, 92]),
    ('P_BFGS-RealAmplitudes', [115, 180]), ('P_BFGS-TwoLocal', [100, 300]), ('P_BFGS-EfficientSU2', [115, 180]),
    ('NELDER_MEAD-RealAmplitudes', [211, 315]), ('NELDER_MEAD-TwoLocal', [211, 315]), ('NELDER_MEAD-EfficientSU2', [211, 315]),
    ('POWELL-RealAmplitudes', [462, 576]), ('POWELL-TwoLocal', [619, 252]), ('POWELL-EfficientSU2', [462, 576])
]

data_3q_function_calls = [
    ('SLSQP-RealAmplitudes', [382, 860]), ('SLSQP-TwoLocal', [510, 1381]), ('SLSQP-EfficientSU2', [519, 625]),
    ('P_BFGS-RealAmplitudes', [5010, 3740]), ('P_BFGS-TwoLocal', [2070, 2770]), ('P_BFGS-EfficientSU2', [1790, 5280]),
    ('NELDER_MEAD-RealAmplitudes', [1000, 1000]), ('NELDER_MEAD-TwoLocal', [1000, 1000]), ('NELDER_MEAD-EfficientSU2', [0, 0]),
    ('POWELL-RealAmplitudes', [1000, 1000]), ('POWELL-TwoLocal', [0, 0]), ('POWELL-EfficientSU2', [0, 0])
]

# Create figure and axes for 6 subplots
fig, axs = plt.subplots(4, 2, figsize=(14, 18), dpi=600)  # Adjusted to 4 rows

# Plot gate counts
plot_metric(data_2q, axs[0, 0], 'gate_count', 'Gate count')
axs[0, 0].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 2$', fontsize=15)
plot_metric(data_3q, axs[0, 1], 'gate_count', 'Gate count')
axs[0, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 3$', fontsize=15)

# Plot circuit depths
plot_metric(circuit_depth_2q, axs[1, 0], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depth_3q, axs[1, 1], 'circuit_depth', 'Circuit depth')

# Plot for function calls (\lambda_0)
plot_metric([(opt, calls[0]) for opt, calls in data_2q_function_calls], axs[2, 0], 'function_calls', r'Function calls ($\lambda_0$)')
plot_metric([(opt, calls[0]) for opt, calls in data_3q_function_calls], axs[2, 1], 'function_calls', r'Function calls ($\lambda_0$)')

# Plot for function calls (\lambda_1)
plot_metric([(opt, calls[1]) for opt, calls in data_2q_function_calls], axs[3, 0], 'function_calls', r'Function calls ($\lambda_1$)')
plot_metric([(opt, calls[1]) for opt, calls in data_3q_function_calls], axs[3, 1], 'function_calls', r'Function calls ($\lambda_1$)')

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.show()

### For V = 10.5 (N = 2 and 3)

### All quantum resources

In [57]:
# Data for 2 qubits
data_2q = [
    ('SLSQP-RealAmplitudes', 5), ('SLSQP-TwoLocal', 5), ('SLSQP-EfficientSU2', 5),
    ('P_BFGS-RealAmplitudes', 5), ('P_BFGS-TwoLocal', 5), ('P_BFGS-EfficientSU2', 5),
    ('NELDER_MEAD-RealAmplitudes', 5), ('NELDER_MEAD-TwoLocal', 5), ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 5), ('POWELL-TwoLocal', 5), ('POWELL-EfficientSU2', 5),
]

# Data for 3 qubits
data_3q = [
    ('SLSQP-RealAmplitudes', 15), ('SLSQP-TwoLocal', 15), ('SLSQP-EfficientSU2', 15),
    ('P_BFGS-RealAmplitudes', 15), ('P_BFGS-TwoLocal', 15),
    ('NELDER_MEAD-RealAmplitudes', 0), ('NELDER_MEAD-TwoLocal', 0), ('NELDER_MEAD-EfficientSU2', 21),
    ('POWELL-RealAmplitudes', 0), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0),
]

# Data for circuit depths
circuit_depth_2q = [('SLSQP-RealAmplitudes', 3), ('SLSQP-TwoLocal', 3), ('SLSQP-EfficientSU2', 3),
                    ('P_BFGS-RealAmplitudes', 3), ('P_BFGS-TwoLocal', 3), ('P_BFGS-EfficientSU2', 3),
                    ('NELDER_MEAD-RealAmplitudes', 3), ('NELDER_MEAD-TwoLocal', 3), ('NELDER_MEAD-EfficientSU2', 3),
                    ('POWELL-RealAmplitudes', 3), ('POWELL-TwoLocal', 3), ('POWELL-EfficientSU2', 3)]

circuit_depth_3q = [('SLSQP-RealAmplitudes', 9), ('SLSQP-TwoLocal', 9), ('SLSQP-EfficientSU2', 9),
                    ('P_BFGS-RealAmplitudes', 9), ('P_BFGS-TwoLocal', 9),
                    ('NELDER_MEAD-RealAmplitudes', 0), ('NELDER_MEAD-TwoLocal', 0), ('NELDER_MEAD-EfficientSU2', 13),
                    ('POWELL-RealAmplitudes', 0), ('POWELL-TwoLocal', 0), ('POWELL-EfficientSU2', 0)]

# Data for function calls (two values for each: \lambda_0 and \lambda_1)
data_2q_function_calls = [
    ('SLSQP-RealAmplitudes', [65, 90]), ('SLSQP-TwoLocal', [90, 89]), ('SLSQP-EfficientSU2', [65, 90]),
    ('P_BFGS-RealAmplitudes', [110, 105]), ('P_BFGS-TwoLocal', [100, 215]), ('P_BFGS-EfficientSU2', [110, 105]),
    ('NELDER_MEAD-RealAmplitudes', [202, 279]), ('NELDER_MEAD-TwoLocal', [202, 279]), ('NELDER_MEAD-EfficientSU2', [202, 279]),
    ('POWELL-RealAmplitudes', [566, 368]), ('POWELL-TwoLocal', [571, 288]), ('POWELL-EfficientSU2', [566, 368])
]

data_3q_function_calls = [
    ('SLSQP-RealAmplitudes', [807, 875]), ('SLSQP-TwoLocal', [644, 854]), ('SLSQP-EfficientSU2', [321, 1540]),
    ('P_BFGS-RealAmplitudes', [1620, 3610]), ('P_BFGS-TwoLocal', [4480, 1340]), ('P_BFGS-EfficientSU2', [1140, 2060]),
    ('NELDER_MEAD-RealAmplitudes', [0, 0]), ('NELDER_MEAD-TwoLocal', [0, 0]), ('NELDER_MEAD-EfficientSU2', [1000, 1000]),
    ('POWELL-RealAmplitudes', [0, 0]), ('POWELL-TwoLocal', [0, 0]), ('POWELL-EfficientSU2', [0, 0])
]

# Create figure and axes for 6 subplots
fig, axs = plt.subplots(4, 2, figsize=(14, 18), dpi=600)  # Adjusted to 4 rows

# Plot gate counts
plot_metric(data_2q, axs[0, 0], 'gate_count', 'Gate count')
axs[0, 0].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 2$', fontsize=15)
plot_metric(data_3q, axs[0, 1], 'gate_count', 'Gate count')
axs[0, 1].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 3$', fontsize=15)

# Plot circuit depths
plot_metric(circuit_depth_2q, axs[1, 0], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depth_3q, axs[1, 1], 'circuit_depth', 'Circuit depth')

# Plot for function calls (\lambda_0)
plot_metric([(opt, calls[0]) for opt, calls in data_2q_function_calls], axs[2, 0], 'function_calls', r'Function calls ($\lambda_0$)')
plot_metric([(opt, calls[0]) for opt, calls in data_3q_function_calls], axs[2, 1], 'function_calls', r'Function calls ($\lambda_0$)')

# Plot for function calls (\lambda_1)
plot_metric([(opt, calls[1]) for opt, calls in data_2q_function_calls], axs[3, 0], 'function_calls', r'Function calls ($\lambda_1$)')
plot_metric([(opt, calls[1]) for opt, calls in data_3q_function_calls], axs[3, 1], 'function_calls', r'Function calls ($\lambda_1$)')

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.show()